In [7]:
# 네이버 검색 API 예제 - 블로그 검색
import os
import sys
import urllib.request, urllib.parse, time
import json
from datetime import datetime
import re
import html
from transformers import AutoTokenizer, AutoModelForSequenceClassification, pipeline
import torch
from sklearn.model_selection import train_test_split
from transformers import TrainingArguments
from transformers import Trainer
from collections import Counter

c:\Users\JU\AppData\Local\Programs\Python\Python311\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [8]:
# from google.colab import drive
# drive.mount('/content/drive')

In [9]:
client_id = "L1c5IBoQZ2wioGa61pTX"
client_secret = "5JtlPeI4Yn"

max_display = 100  # 한 번에 가져올 결과 개수

new_description = dict()
idx = 0

In [10]:
# 100번 반복하여 100개씩 요청 (총 10000개 결과)

for t in ["범죄", "전쟁", "징역", "사고", "폭력", "재난", "사망", "파괴", "분쟁", "테러", "부도", "부패", "봉사", "구조", "산업", "발전", "혁신", "성공", "희망", "협력"]:
    encText = urllib.parse.quote(t)
    for i in range(10): #1페이지에 100개, 10번
        start = 1 + i * max_display
        url = f"https://openapi.naver.com/v1/search/news?query={encText}&display={max_display}&start={start}&sort=sim"

        request = urllib.request.Request(url)
        request.add_header("X-Naver-Client-Id", client_id)
        request.add_header("X-Naver-Client-Secret", client_secret)

        response = urllib.request.urlopen(request)
        rescode = response.getcode()

        if rescode == 200:
            response_body = response.read()  # 바이트 데이터 읽기
            response_json = json.loads(response_body.decode("utf-8"))  # JSON 변환

            for item in response_json["items"]:
                # 제목과 설명 합치기
                text = item['title'] + item['description']
                # HTML 엔티티 복원
                text = html.unescape(text)
                # HTML 태그 제거
                text = re.sub(r"<.*?>", "", text)
                text = text.replace(".", "")
                new_description[idx] = [text, item['link']]
                idx += 1
        else:
            print(f"Error Code: {rescode}")

        # API 요청 제한에 걸리지 않도록 잠시 대기 (필요시 조정)
        time.sleep(0.5)

In [11]:
# 결과 출력 예시
for i in range(0, 20000, 1000):
  print(new_description[i])

['권성동 "선관위는 범죄 마피아 패밀리…채용비리 국정조사해야"그는 "선관위는 친인척 채용 논란이 생기자 서류 파기를 지시하는 등 범죄 행위의 은폐를 시도했다"며 "이쯤 되면 선거를 관리하는 조직인지, 범죄 마피아 패밀리인지 헷갈릴 지경"이라고 비판했다 전날 헌법재판소가 ', 'https://n.news.naver.com/mnews/article/003/0013093608?sid=100']
["16개월만 감소 돌아선 반도체 수출…미중 관세전쟁 유탄 우려도'중국 공세' 범용 메모리 반도체 가격 하락 여파…미중 무역전쟁도 영향 가능성 올해 들어 수출 증가율 '뚝 게다가 향후 트럼프 2기 미중 관세 전쟁이 격화하면서 한국의 대(對)중국 반도체 중간재 수출에도 타격이 ", 'https://n.news.naver.com/mnews/article/001/0015240989?sid=105']
["'쓰러진 여성에 발길질' 징역 25년 40대 대법원에 상고처음 본 여성을 흉기로 위협해 골목길로 끌고 가 발로 얼굴을 차는 등 무차별 폭행으로 징역 25년을 A씨는 지난해 8월 강도살인미수혐의로 재판에 기소돼 징역 25년을 선고 받았다 그는 항소에 곧바로 나섰지만 지난 ", 'https://n.news.naver.com/mnews/article/421/0008105703?sid=102']
['통영대전고속도로서 5중 추돌사고…5명 부상▲ 5중 추돌사고 현장 어제(28일) 새벽 1시 30분쯤 경남 진주시 명석면 통영대전고속도로 통영 방면 산청3터널 부근에서 5중 추돌 사고가 났습니다 경남경찰청에 따르면 50대 운전자 A 씨가 몰던 승용차가 중앙분리대를 ', 'https://n.news.naver.com/mnews/article/055/0001236208?sid=102']
["탄핵찬반 집회로 갈라진 대학가…입학식날 폭력사태 '얼룩'(종합)성균관대에 '부정선거론' 황교안 등장…외대·시립대서도 대치 김준태 이율립 기자 = 윤석열 대통령 탄핵을 둘러싼 찬반 집회가 28일 서울 동북권의 대학들

In [12]:
# KcBERT 모델과 토크나이저 로드
model_name = "monologg/koelectra-base-finetuned-nsmc"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSequenceClassification.from_pretrained(model_name)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

# 저장된 가중치 경로
#checkpoint_path = "/content/drive/MyDrive/nsmc-master/models/news_sentiment_model_0201_01.pth"

# # 모델 가중치 로드 (환경에 맞게 자동 설정)
# if os.path.exists(checkpoint_path):
#     model.load_state_dict(torch.load(checkpoint_path, map_location=device))
#     model.to(device)  # 모델을 현재 사용 가능한 장치로 이동
#     print(f"모델 가중치가 성공적으로 로드되었습니다: {checkpoint_path} (장치: {device})")
# else:
#     print(f"가중치 파일이 존재하지 않습니다: {checkpoint_path}")


ElectraForSequenceClassification(
  (electra): ElectraModel(
    (embeddings): ElectraEmbeddings(
      (word_embeddings): Embedding(32200, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): ElectraEncoder(
      (layer): ModuleList(
        (0-11): 12 x ElectraLayer(
          (attention): ElectraAttention(
            (self): ElectraSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): ElectraSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): L

In [13]:
print(len(new_description.values()))

20000


In [14]:
import json

# 긍정 뉴스와 부정 뉴스를 각각 저장할 리스트 생성 (딕셔너리 형태)
positive_results = []
negative_results = []

# 감정분석 파이프라인 생성 (모델 출력은 [{'label': ..., 'score': ...}] 형태입니다)
sentiment_analyzer = pipeline("sentiment-analysis", model=model, tokenizer=tokenizer)

for news in new_description.values():
    # 뉴스 텍스트에 대해 감정분석 수행
    analysis = sentiment_analyzer(news[0])
    prediction = analysis[0]

    # negative 라벨은 score가 0.9 초과인 경우에만 부정으로 저장
    if prediction['label'].lower() == "negative" and prediction['score'] > 0.8:
        negative_results.append({
            "text": news[0],
            "label": "부정"
        })
    # positive 라벨은 score가 0.95 초과인 경우에만 긍정으로 저장
    elif prediction['label'].lower() == "positive" and prediction['score'] > 0.95:
        positive_results.append({
            "text": news[0],
            "label": "긍정"
        })
    else:
        continue  # 조건에 맞지 않는 경우는 건너뜁니다.

# 최종 JSON 데이터 (긍정과 부정 따로)
final_json = {
    "긍정": positive_results,
    "부정": negative_results
}

# JSON 문자열로 출력 (한글이 깨지지 않도록 ensure_ascii=False)
print(json.dumps(final_json, indent=4, ensure_ascii=False))


Device set to use cuda:0
You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


{
    "긍정": [
        {
            "text": "멕시코 \"미국이 범죄인 29명 인도 요청해와…국가안보위해 합의\"29명의 범죄인을 미국에 인도한 조처와 관련, \"국가안보를 위해 합의를 거쳐 내린 결정\"이라고 강조했다 기자회견에서 \"미국에서 범죄인 29명에 대한 인도를 요청했다\"며 \"모든 절차는 합법적 틀 내에서 이뤄졌다\"고 ",
            "label": "긍정"
        },
        {
            "text": "서울 남부지검에 가상자산범죄합동수사부 정식 출범…\"투자자 보호에 최가상자산 범죄를 수사하는 검찰 조직인 가상자산범죄합동수사부가 정식 직제화 돼 출범했다 서울남부지검은 27일 임시 조직으로 운영되던 가상자산범죄합동수사단(합수단)이 정식 부서인 가상자산범죄합동수사부 ",
            "label": "긍정"
        },
        {
            "text": "서울남부지검, 가상자산범죄합동수사부 출범27일 서울남부지검은 가상자산범죄합동수사부(합수부) 출범식을 열었다 2023년 7월 임시조직으로 출발한 가상자산범죄합동수사단이 지난 25일 정식 부서로 승격한 것이다 검찰 관계자는 “가상자산 시장의 규모가 ",
            "label": "긍정"
        },
        {
            "text": "코인시장 범죄 대응 위한 검찰 '합동수사부' 정식 출범급증하는 가상자산 범죄에 대응하기 위해 서울 남부지검이 임시 조직으로 운영되던 가상자산범죄합동수사단을 정식 부서인 합동수사부로 승격시켰다고 밝혔습니다 가장자산범죄합동수사부는 검찰 수사관과 금융당국 ",
            "label": "긍정"
        },
        {
            "text": "독가스와 노예노동으로 100만 명 숨진 '죽음의 수용소' 아우슈비츠[김재독일의 전쟁범죄-홀로코스트 36 \"(히틀러) 총통께서는 유대인 문제를 단숨에 

In [ ]:
import json

# 저장할 파일 경로
file_path = "beaming/data/train_over09.json"

# JSON 파일로 저장
with open(file_path, "w", encoding="utf-8") as f:
    json.dump(final_json, f, ensure_ascii=False, indent=4)

print(f"JSON 파일이 '{file_path}'에 저장되었습니다.")

JSON 파일이 'beaming/data/train_over09.json'에 저장되었습니다.


In [21]:
file_path = 'data/train_over09.json'
with open(file_path, 'r', encoding='utf-8') as file:
    data = json.load(file)

print(data)

{'긍정': [{'text': '멕시코 "미국이 범죄인 29명 인도 요청해와…국가안보위해 합의"29명의 범죄인을 미국에 인도한 조처와 관련, "국가안보를 위해 합의를 거쳐 내린 결정"이라고 강조했다 기자회견에서 "미국에서 범죄인 29명에 대한 인도를 요청했다"며 "모든 절차는 합법적 틀 내에서 이뤄졌다"고 ', 'label': '긍정'}, {'text': '서울 남부지검에 가상자산범죄합동수사부 정식 출범…"투자자 보호에 최가상자산 범죄를 수사하는 검찰 조직인 가상자산범죄합동수사부가 정식 직제화 돼 출범했다 서울남부지검은 27일 임시 조직으로 운영되던 가상자산범죄합동수사단(합수단)이 정식 부서인 가상자산범죄합동수사부 ', 'label': '긍정'}, {'text': '서울남부지검, 가상자산범죄합동수사부 출범27일 서울남부지검은 가상자산범죄합동수사부(합수부) 출범식을 열었다 2023년 7월 임시조직으로 출발한 가상자산범죄합동수사단이 지난 25일 정식 부서로 승격한 것이다 검찰 관계자는 “가상자산 시장의 규모가 ', 'label': '긍정'}, {'text': "코인시장 범죄 대응 위한 검찰 '합동수사부' 정식 출범급증하는 가상자산 범죄에 대응하기 위해 서울 남부지검이 임시 조직으로 운영되던 가상자산범죄합동수사단을 정식 부서인 합동수사부로 승격시켰다고 밝혔습니다 가장자산범죄합동수사부는 검찰 수사관과 금융당국 ", 'label': '긍정'}, {'text': '독가스와 노예노동으로 100만 명 숨진 \'죽음의 수용소\' 아우슈비츠[김재독일의 전쟁범죄-홀로코스트 36 "(히틀러) 총통께서는 유대인 문제를 단숨에 해결하라 하셨네 그렇기에 저질렀던 범죄를 부인했다 헤르만 괴링을 비롯한 지도급 인물들은 "우리가 피고석에 선 것은 전쟁에서 졌기 ', 'label': '긍정'}, {'text': '제주경찰 "외국인 강력범죄 구속 수사 원칙…시민 안전 확보"제주경찰청은 28일 제주도민과 관광객 안전을 위해 외국인 강력범죄에 강력히 대응하겠다고 밝혔다 제주경찰청은 "최근 외국인 강

In [17]:
print(len(data["긍정"]) ,len(data["부정"]))

8649 1954


In [18]:
print(len(final_json["긍정"]) ,len(final_json["부정"]))

8649 1954


In [22]:
# 1. 데이터 불러오기
data_path = "data/train_over09.json"
with open(data_path, "r", encoding="utf-8") as f:
    data = json.load(f)

texts = []
labels = []
# 여기서는 "긍정"은 1, "부정"은 0으로 매핑
for label_str, examples in data.items():
    for example in examples:
        texts.append(example["text"])
        labels.append(1 if label_str == "긍정" else 0)

In [23]:
# 2. 학습/검증 데이터셋 분할 (예: 90% 학습, 10% 검증)
train_texts, val_texts, train_labels, val_labels = train_test_split(
    texts, labels, test_size=0.1, random_state=42, stratify=labels
)

In [24]:
# 3. 토크나이저 로드 및 토큰화
model_name = "klue/roberta-large"
tokenizer = AutoTokenizer.from_pretrained(model_name)

def tokenize_texts(text_list):
    return tokenizer(text_list, padding="max_length", truncation=True, max_length=256)

train_encodings = tokenize_texts(train_texts)
val_encodings = tokenize_texts(val_texts)

c:\Users\JU\AppData\Local\Programs\Python\Python311\Lib\site-packages\huggingface_hub\file_download.py:140: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\JU\.cache\huggingface\hub\models--klue--roberta-large. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


In [25]:
# 4. PyTorch 데이터셋 클래스 정의
class NewsSentimentDataset(torch.utils.data.Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels
    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        item["labels"] = torch.tensor(self.labels[idx])
        return item
    def __len__(self):
        return len(self.labels)

train_dataset = NewsSentimentDataset(train_encodings, train_labels)
val_dataset = NewsSentimentDataset(val_encodings, val_labels)

In [26]:
# 5. 모델 로드 (분류 head가 포함된 모델)
model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=2)

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at klue/roberta-large and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [27]:
# 6. 클래스 불균형을 반영한 가중치 계산
train_counts = Counter(train_labels)  # 예: {1: 8684, 0: 1934}
total_train = len(train_labels)
num_classes = 2
# 가중치는 total / (num_classes * count) 공식 사용
weights = [total_train / (num_classes * train_counts[i]) for i in range(num_classes)]
# 예: weight[0] (부정): 약 2.74, weight[1] (긍정): 약 0.61
class_weights = torch.tensor(weights, dtype=torch.float)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
class_weights = class_weights.to(device)


In [28]:
class WeightedLossTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False, **kwargs):
        labels = inputs.get("labels")
        outputs = model(**inputs)
        logits = outputs.get("logits")
        loss_fct = torch.nn.CrossEntropyLoss(weight=class_weights)
        loss = loss_fct(logits, labels)
        return (loss, outputs) if return_outputs else loss


In [ ]:
training_args = TrainingArguments(
    output_dir="beaming/robert_about",
    num_train_epochs=3,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=64,
    warmup_steps=500,
    weight_decay=0.01,
    evaluation_strategy="epoch",
    logging_dir="beaming/robert_about",
    logging_steps=10,
    save_total_limit=2,
    report_to=[]  # wandb 등 로깅 툴 사용 안함
)


ValueError: You have set `args.eval_strategy` to IntervalStrategy.EPOCH but you didn't pass an `eval_dataset` to `Trainer`. Either set `args.eval_strategy` to `no` or pass an `eval_dataset`. 

In [30]:
# 9. Trainer 생성 (WeightedLossTrainer 사용)
trainer = WeightedLossTrainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    tokenizer=tokenizer,
)

C:\Users\JU\AppData\Local\Temp\ipykernel_21556\3729113739.py:2: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `WeightedLossTrainer.__init__`. Use `processing_class` instead.
  trainer = WeightedLossTrainer(


In [ ]:
# 10. 파인튜닝 실행
trainer.train()

In [ ]:
# 저장된 모델 디렉토리 경로
model_path = "/content/drive/MyDrive/nsmc-master/models/robert_about/checkpoint-598"

# 토크나이저와 모델 불러오기
tokenizer = AutoTokenizer.from_pretrained(model_path)
model = AutoModelForSequenceClassification.from_pretrained(model_path)

# 파이프라인 생성 (예: 감성 분석)
nlp = pipeline("sentiment-analysis", model=model, tokenizer=tokenizer)


In [ ]:

# 예시 문장에 대해 예측해보기
text = ""'''도박 빚 갚아달라' 엄마·외조모 흉기 폭행한 20대 징역형 집유춘천지법 원주지원 형사2단독 박현진 부장판사는 특수존속협박·폭행 혐의로 기소된 A(25)씨에게 징역 1년 6월에 집행유예 3년을 선고하고 보호관찰을 명령했다고 1일 밝혔다 A씨는 지난해 4월 20일 모친에게 도박 빚을"'''
result = nlp(text)
print(result)

In [ ]:
# 100번 반복하여 100개씩 요청 (총 10000개 결과)
testing = dict()
idx = 0
for t in ["여행"]: #"범죄", "전쟁", "징역", "사고", "폭력", "재난", "사망", "파괴", "분쟁", "테러", "부도", "부패", "봉사", "구조", "산업", "발전", "혁신", "성공", "희망", "협력"
    encText = urllib.parse.quote(t)
    for i in range(10): #1페이지에 100개, 10번
        start = 1 + i * max_display
        url = f"https://openapi.naver.com/v1/search/news?query={encText}&display={max_display}&start={start}&sort=sim"

        request = urllib.request.Request(url)
        request.add_header("X-Naver-Client-Id", client_id)
        request.add_header("X-Naver-Client-Secret", client_secret)

        response = urllib.request.urlopen(request)
        rescode = response.getcode()

        if rescode == 200:
            response_body = response.read()  # 바이트 데이터 읽기
            response_json = json.loads(response_body.decode("utf-8"))  # JSON 변환

            for item in response_json["items"]:
                # 제목과 설명 합치기
                text = item['title'] + item['description']
                # HTML 엔티티 복원
                text = html.unescape(text)
                # HTML 태그 제거
                text = re.sub(r"<.*?>", "", text)
                text = text.replace(".", "")
                testing[idx] = [text, item['link']]
                idx += 1
        else:
            print(f"Error Code: {rescode}")

        # API 요청 제한에 걸리지 않도록 잠시 대기 (필요시 조정)
        time.sleep(0.5)


In [ ]:
testing

In [ ]:
for item in testing.values():
    print(nlp(item[0]))
    print(item[0])
    print("---------------")

In [ ]:
positive_items = []
negative_items = []

# testing은 텍스트를 담고 있는 딕셔너리라고 가정합니다.
for item in testing.values():
    result = nlp(item[0])
    # nlp 함수의 결과는 [{'label': 'LABEL_X', 'score': ...}] 형식입니다.
    label = result[0]['label']
    score = result[0]['score']

    # 라벨 매핑: LABEL_1 -> 긍정, LABEL_0 -> 부정
    mapped_label = "긍정" if label == "LABEL_1" else "부정"

    # 긍정, 부정에 따라 리스트에 추가
    if mapped_label == "긍정" and score >= 0.9:
        positive_items.append((mapped_label, score, item[0]))
    elif  mapped_label == "부정" and score >= 0.9:
        negative_items.append((mapped_label, score, item[0]))

# 긍정 결과 출력
print("긍정 결과:")
for label, score, text in positive_items:
    print(f"{label}, score: {score}")
    print(text)
    print("---------------")

# 부정 결과 출력
print("부정 결과:")
for label, score, text in negative_items:
    print(f"{label}, score: {score}")
    print(text)
    print("---------------")

print(len(positive_items), len(negative_items))